In [0]:
!pip install --upgrade pip

Requirement already satisfied: pip in /databricks/python3/lib/python3.8/site-packages (21.0.1)
Collecting pip
 Using cached pip-22.3.1-py3-none-any.whl (2.1 MB)
Installing collected packages: pip
 Attempting uninstall: pip
 Found existing installation: pip 21.0.1
 Uninstalling pip-21.0.1:
 Successfully uninstalled pip-21.0.1
Successfully installed pip-22.3.1

In [0]:
!pip install msal

Collecting msal
 Using cached msal-1.20.0-py2.py3-none-any.whl (90 kB)
Requirement already satisfied: requests<3,>=2.0.0 in /databricks/python3/lib/python3.8/site-packages (from msal) (2.25.1)
Collecting cryptography<41,>=0.6
 Using cached cryptography-38.0.4-cp36-abi3-manylinux_2_28_x86_64.whl (4.2 MB)
Collecting PyJWT[crypto]<3,>=1.0.0
 Using cached PyJWT-2.6.0-py3-none-any.whl (20 kB)
Requirement already satisfied: cffi>=1.12 in /databricks/python3/lib/python3.8/site-packages (from cryptography<41,>=0.6->msal) (1.14.5)
Requirement already satisfied: urllib3<1.27,>=1.21.1 in /databricks/python3/lib/python3.8/site-packages (from requests<3,>=2.0.0->msal) (1.25.11)
Requirement already satisfied: idna<3,>=2.5 in /databricks/python3/lib/python3.8/site-packages (from requests<3,>=2.0.0->msal) (2.10)
Requirement already satisfied: certifi>=2017.4.17 in /databricks/python3/lib/python3.8/site-packages (from requests<3,>=2.0.0->msal) (2020.12.5)
Requirement already satisfied: chardet<5,>=3.0.2 in /databricks/python3/lib/python3.8/site-packages (from requests<3,>=2.0.0->msal) (4.0.0)
Requirement already satisfied: pycparser in /databricks/python3/lib/python3.8/site-packages (from cffi>=1.12->cryptography<41,>=0.6->msal) (2.20)
Installing collected packages: PyJWT, cryptography, msal
Successfully installed PyJWT-2.6.0 cryptography-38.0.4 msal-1.20.0

In [0]:
import msal
import pandas as pd
from pandas import DataFrame
import pyspark
from pyspark.sql import SparkSession
import pyspark.sql.utils
from pyspark.sql.functions import explode
from pyspark.sql.types import DoubleType
import  warnings
warnings.filterwarnings('ignore')

In [0]:
conta = 'stgestudos'
container = 'marcell-felipe-oliveira'
chave = dbutils.secrets.get('scope-adb-estudos', key = 'acess-key-blob-v1')


In [0]:
def sub_unmount(str_path):
    if any(mount.mountPoint == str_path for mount in dbutils.fs.mounts()):
        dbutils.fs.unmount(str_path)
        
sub_unmount('/mnt/marcell-felipe-oliveira')

/mnt/marcell-felipe-oliveira has been unmounted.

In [0]:
dbutils.fs.mount(
    source = f"wasbs://{container}@{conta}.blob.core.windows.net",
    mount_point = f"/mnt/marcell-felipe-oliveira",
    extra_configs = {f"fs.azure.account.key.{conta}.blob.core.windows.net": chave}
)

Out[6]: True

In [0]:
spark = SparkSession.builder.getOrCreate()
df_eventos = spark.read.json('/mnt/marcell-felipe-oliveira/Lab04/eventos.json').toPandas()

In [0]:
df_eventos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1498 entries, 0 to 1497
Data columns (total 14 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 classificacaoEtaria 1498 non-null object
 1 createTimestamp 1498 non-null object
 2 descricaoSonora 454 non-null object
 3 id 1498 non-null int64 
 4 longDescription 1497 non-null object
 5 name 1498 non-null object
 6 registrationInfo 523 non-null object
 7 shortDescription 1498 non-null object
 8 site 468 non-null object
 9 subTitle 813 non-null object
 10 telefonePublico 1013 non-null object
 11 terms 1498 non-null object
 12 traducaoLibras 469 non-null object
 13 updateTimestamp 1466 non-null object
dtypes: int64(1), object(13)
memory usage: 164.0+ KB

In [0]:
df_eventos = df_eventos.rename({'id': 'event_Id'}, axis=1)
df_eventos.sample()

Out[9]:

classificacaoEtaria 
 createTimestamp 
 descricaoSonora 
 event_Id 
 longDescription 
 name 
 registrationInfo 
 shortDescription 
 site 
 subTitle 
 telefonePublico 
 terms 
 traducaoLibras 
 updateTimestamp 
 
 
 
 
 206 
 Livre 
 {'date': '2018-01-23 10:34:42.000000', 'timezo... 
 None 
 2167 
 
 Exposição itinerante: Mostra do Centro de Memó... 
 None 
 Mostra inserida na 11ª Primavera dos Museus, r... 
 None 
 None 
 None 
 {'linguagem': ['Exposição'], 'tag': ['adminibr... 
 None 
 {'date': '2018-01-23 10:36:40.000000', 'timezo...

In [0]:
def tratNulos(df, col, texto):
    df[col][(df[col].isna()) | (df[col]=='') | (df[col]==' ')] = texto

In [0]:
df_eventos.classificacaoEtaria.value_counts()

Out[11]: Livre 1382
16 anos 35
18 anos 34
10 anos 17
14 anos 17
12 anos 13
Name: classificacaoEtaria, dtype: int64

In [0]:
df_eventos.drop('createTimestamp',axis =1,inplace = True)
df_eventos.drop('updateTimestamp',axis =1,inplace = True)
df_eventos.drop('registrationInfo',axis =1,inplace = True)
df_eventos.drop('terms',axis =1,inplace = True)

In [0]:
df_eventos.sample()

Out[13]:

classificacaoEtaria 
 descricaoSonora 
 event_Id 
 longDescription 
 name 
 shortDescription 
 site 
 subTitle 
 telefonePublico 
 traducaoLibras 
 
 
 
 
 1254 
 18 anos 
 None 
 6322 
 O tema do Mangue – zona de prostituição no Rio... 
 O Mangue de Segall, entre amigos poetas e uma ... 
 O curso aborda o álbum "Mangue" de Lasar segal... 
 https://mls.gov.br 
 Dias 21 e 28/09 de 2019 
 (11) 2159-0400 
 None

In [0]:
tratNulos(df_eventos,'descricaoSonora','Não informado')
df_eventos['descricaoSonora'].head(10)

Out[14]: 0 Não
1 Não informado
2 Não informado
3 Não informado
4 Não informado
5 Não informado
6 Não informado
7 Não
8 Não informado
9 Não informado
Name: descricaoSonora, dtype: object

In [0]:
df_eventos.drop(764, inplace = True) 

In [0]:
tratNulos(df_eventos,'site','Não informado')
df_eventos["site"].head(10)

Out[16]: 0 Não informado
1 Não informado
2 http://www.museunacionaldapoesia.blogspot.com
3 http://www.fmrb.ma.gov.br
4 https://www.facebook.com/ecomuseunaturaldomang...
5 Não informado
6 Não informado
7 https://www.facebook.com/events/1738599869773715
8 http://www.mcb.org.br
9 http://www.mcb.org.br
Name: site, dtype: object

In [0]:
tratNulos(df_eventos,'longDescription','Não informado')
tratNulos(df_eventos,'traducaoLibras','Não informado')
tratNulos(df_eventos,'telefonePublico','Não informado')
df_eventos.sample(10)

Out[17]:

classificacaoEtaria 
 descricaoSonora 
 event_Id 
 longDescription 
 name 
 shortDescription 
 site 
 subTitle 
 telefonePublico 
 traducaoLibras 
 
 
 
 
 119 
 Livre 
 Não 
 2053 
 O quilombo indígena está localizado na Serra d... 
 Exposição Tiririca dos Crioulos 
 A exposição Tiririca dos Crioulos apresenta o ... 
 Não informado 
 Pessoas fortes na Luta 
 (81) 3228-3248 
 Não 
 
 
 34 
 Livre 
 Não informado 
 1407 
 Com 39 anos de pesquisas, ensaios e shows, o D... 
 Música no MCB | Duofel 
 Com 39 anos de pesquisas, ensaios e shows, o D... 
 http://www.mcb.org.br 
 None 
 (11) 3032-3727 
 Não informado 
 
 
 273 
 Livre 
 Não informado 
 2617 
 Pretende também aumentar a conscientização nos... 
 "MOW BRASIL" - DIA 04/06/2018 das 09:00 h às 1... 
 O Programa Memória do Mundo da UNESCO – MoW, –... 
 Não informado 
 COMITÊ MOWBRASIL 
 (21) 3299-0300 
 Não informado 
 
 
 884 
 Livre 
 Não 
 4824 
 Leitura da obra "Quatorze Quadros Redondos" de... 
 Leitura Dramatizada: "Quatorze Quadros Quebrados" 
 Leitura Dramatizada de poemas do livro “Quator... 
 Não informado 
 None 
 Não informado 
 Não 
 
 
 889 
 Livre 
 Não informado 
 4829 
 Não informado 
 Os Imigrantes e a Formação de Petrópolis 
 Exposição que conta a trajetória de grupos que... 
 Não informado 
 None 
 Não informado 
 Não informado 
 
 
 578 
 Livre 
 Não informado 
 4176 
 No dia 09 de abril/2018 no auditório do Museu ... 
 PROGRAMA DE QUALIFICAÇÃO NOS MUSEUS DE ALCÂNTARA 
 O arqueólogo Deusdétit Carneiro do Centro de H... 
 Não informado 
 Palestra sobre os povos indígenas do Maranhão 
 Não informado 
 Não informado 
 
 
 696 
 Livre 
 Não informado 
 4549 
 Não informado 
 Curso de Extenção 2018 - Tópicos da História ... 
 Curso de Extenção 2018 - Tópicos da História ... 
 Não informado 
 Conversas sobre o Candomblé e Psicologia Analí... 
 (81) 3228-3248 
 Não informado 
 
 
 770 
 Livre 
 Não informado 
 4695 
 Não informado 
 Férias no Museu 
 Realização de brincadeiras infantis tradiciona... 
 Não informado 
 None 
 Não informado 
 Não informado 
 
 
 123 
 Livre 
 Não informado 
 2057 
 sta Mostra apresenta um panorama da produção d... 
 Exposição "Idas e vindas: Segall e o Brasil" 
 Esta Mostra apresenta um panorama da produção ... 
 Não informado 
 None 
 (11) 2159-0400 
 Não informado 
 
 
 1120 
 Livre 
 Não 
 5813 
 Não informado 
 Mesa Redonda 
 Mesa Redonda discutindo o tema 'O Carnaval na ... 
 Não informado 
 None 
 Não informado 
 Não

In [0]:
df_eventos.drop('subTitle',axis =1,inplace = True)

In [0]:
df_eventos.display()

classificacaoEtaria descricaoSonora event_Id longDescription name shortDescription site telefonePublico traducaoLibras Livre Não 448 Oficialmente, a história do esporte começou a ser escrita nos primórdios do século XX, após a fundação do São José Futebol Clube, atual Associação Esportiva São José, ocorrida em 1913. Como não poderia ser diferente, tudo começou com o futebol - em priscas eras – denominado “o esporte bretão”, já naquele tempo, o esporte preferido dos brasileiros.

Informações colhidas do Tablóide Informativo da AESJ nos levam a saber que “por conta do interesse despertado, em São José dos Campos, transformados em “players” jovens daquela época “pentapebolavam” ora na Praça Valeriana , ora no Pátio do Cemitério, em áreas ociosas transformadas em “grounds” improvisados”.

Nascida aos pés da Serra da Mantiqueira, de bucólica cidade à “capital da tecnologia”; do futebol à natação, feminino e masculino, passando por voleibol, tênis, ciclismo, judô, atletismo, basquetebol, futebol de salão, entre tantos outros, São José dos Campos se transformaria ao longo do tempo, num dos principais exportadores de talentos esportivos do País.

Parte integrante deste contexto, o Museu de Esportes de São José dos Campos, vinculada à Secretaria de Esportes e Lazer foi criado com o intuito de resgatar a história esportiva do município, levando além-fronteiras os feitos de seus atletas através de site, palestras ao vivo, depoimento audiovisuais, troféus e exposições fotográficas. São José de todos os esportes Estrategicamente montada no corredor central, a exposição São José de todos os esportes retrata a memória esportiva da cidade a partir da fundação da Associação Esportiva São José, iniciada em 1913 até idos de 2010. Fotos, diplomas e cartazes expostos em ordem alfabética ajudam a resgatar a história do esporte de São José dos Campos, assim como a dos personagens que a representam. Não informado (12) 3921-4112 Não 10 anos Não informado 473 Neste ano proporemos, através deste, as intervenções em sala de aula com o trabalho do poeta potiguar Antônio Francisco, cujo legado e conhecimento são consideravelmente relevantes para a produção literária potiguar, incentivando em nossos educandos a produção literária, o gosto pela leitura e, em especial, o despertar para a cultura popular, cuja qual estes podem identificar-se enquanto agentes ativos de edificação. FESTA DA POESIA Este evento surge como promotor de processos interculturais, uma vez que, há um intercâmbio entre as artes e com o ensino de literatura, pois sem a conversa com os profissionais da educação este seria inconcebível. Buscaremos, desta forma, conscientizar e aproximar o público alvo perpetuando os valores da cultura popular bastante presentes nas atuações do departamento realizadas em Patu. Não informado (84) 99667-0060 Não informado Livre Não informado 988 Sementes de Poesia em homenagem ao Samba e Tango - participação de Olga Valeska e Bruno Braga, uma realização do – Museu Nacional da Poesia – MUNAP sob curadoria de Regina Mello. Domingo, 16 de julho de 2017, 10h às 12h, a 108ª- edição do encontro ao ar livre com microfone aberto. Espaço MUNAP na Praça dos Fundadores, Parque Municipal René Américo Reune Giannetti. entrada franca Sementes de Poesia Neste domingo, 16 de julho de 2017 de 10 às 12h
Sementes de Poesia, microfone aberto ao público todo terceiro domingo do mês, na Praça dos Fundadores, Parque Municipal Américo René Giannetti. Av. Afonso Pena, 1377, centro, BH/MG http://www.museunacionaldapoesia.blogspot.com (31) 98838-7367 Não informado 14 anos Não informado 1044 FUNDAÇÃO DA MEMÓRIA REPUBLICANA BRASILEIRA

Promove Curso de férias no Museu.

🎨 Curso de desenho e pintura (até 14 anos): Dias 24 a 27 de julho - 14:30 às 16:30. Prof Svetlana Farias

🎲 Oficina de jogos (6 a 10 anos) Dias 24 a 27 de julho - 14:30 às 16:30. Prof Larissa Diniz

📒 Curso de encadernação básica (livre). Dias 25 e 26 de julho - 14:30 às 16:30. Prof Heloisa Bruzaca

🔴 Venha fazer sua inscr

In [0]:
df_occurrence = spark.read.json('/mnt/marcell-felipe-oliveira/Lab04/occurences.json')

from pyspark.sql.functions import col

df_occurrence = df_occurrence.select(col('id'), explode('occurrences').alias('occurrences'))

df_occurrence.display()



id occurrences 1325 List(null, null, null, 1325, daily, 739, List(null, Diariamente de 6 de setembro a 22 de outubro de 2017 às 10:00, 480, 18:00, daily, De terça a sexta: R$ 10 e R$ 5 (meia-entrada). Gratuito aos sábados, domingos e feriados, 202940, 10:00, 2017-09-06, 2017-10-22), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1327 List(null, null, null, 1327, weekly, 742, List({"2":"on"}, 5 e 19 de setembro, terças-feiras às 11h, 120, 13:00, weekly, Gratuito, 202940, 11:00, 2017-09-05, 2017-09-19), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1328 List(null, null, null, 1328, weekly, 743, List({"3":"on"}, 6 e 20 de setembro, quartas-feiras às 10h30, 90, 12:00, weekly, Gratuito, 202940, 10:30, 2017-09-06, 2017-09-20), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1329 List(null, null, null, 1329, weekly, 744, List({"3":"on"}, 13 e 27 de setembro, quartas-feiras às 10h30, 90, 12:00, weekly, Gratuito, 202940, 10:30, 2017-09-13, 2017-09-27), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1330 List(null, null, null, 1330, once, 745, List(null, Dia 14 de setembro de 2017 às 13:30, 90, 15:00, once, Gratuito, 202940, 13:30, 2017-09-14, ), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1331 List(null, null, null, 1331, weekly, 746, List({"4":"on"}, Toda quinta-feira de 21 a 28 de setembro de 2017 às 10:30, 90, 12:00, weekly, Gratuito, 202940, 10:30, 2017-09-21, 2017-09-28), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1333 List(null, null, null, 1333, once, 748, List(null, Dia 10 de setembro de 2017 às 14:30, 90, 16:00, once, Gratuito, 202940, 14:30, 2017-09-10, ), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1334 List(null, null, null, 1334, weekly, 749, List({"3":"on"}, Toda quarta-feira de 13 a 27 de setembro de 2017 às 19:00, 120, 21:00, weekly, Gratuito, 202940, 19:00, 2017-09-13, 2017-09-27), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1345 List(null, null, null, 1345, once, 758, List(null, Dia 30 de setembro de 2017 às 14:30, 120, 16:30, once, Gratuito, 202940, 14:30, 2017-09-30, ), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1347 List(null, null, null, 1347, daily, 760, List(null, Diariamente de 2 a 3 de dezembro de 2017 às 10:00, 600, 20:00, daily, Gratuito, 202940, 10:00, 2017-12-02, 2017-12-03), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1348 List(null, null, null, 1348, once, 761, List(null, Dia 10 de setembro de 2017 às 11:00, 90, 12:30, once, Gratuito, 202940, 11:00, 2017-09-10, ), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1349 List(null, null, null, 1349, once, 762, List(null, Dia 17 de setembro de 2017 às 11:00, 90, 12:30, once, Gratuito, 202940, 11:00, 2017-09-17, ), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1350 List(null, null, null, 1350, once, 763, List(null, Dia 24 de setembro de 2017 às 11:00, 90, 12:30, once, Gratuito, 202940, 11:00, 2017-09-24, ), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1373 List(null, null, null, 1373, weekly, 783, List({"0":"on","2":"on","3":"on","4":"on","5":"on","6":"on"}, Todo dom, ter, qua, qui, sex e sáb de 1 de junho a 20 de agosto de 2017 às 10:00, 480, 18:00, weekly, De terça a sexta: R$ 10 e R$ 5 (meia-entrada). Gratuito aos sábados, domingos e feriados, 202940, 10:00, 2017-06-01, 2017-08-20), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1374 List(null, null, null, 1374, weekly, 784, List({"0":"on","2":"on","3":"on","4":"on","5":"on","6":"on"}, Todo dom, ter, qua, qui, sex e sáb de 24 de junho a 13 de agosto de 2017 às 10:00, 480, 18:00, weekly, De terça a sexta: R$ 10 e R$ 5 (meia-entrada). Gratuito aos sábados, domingos e feriados, 202940, 10:00, 2017-06-24, 2017-08-13), 1, 202940, 202940, null, null, 1, null, Etc/UTC, null) 1375 List(null, null, null, 1375, weekly, 785, List({"3":"on"}, 2 e 26 de agosto, quartas-feiras às 10h30, 90, 12:00, weekly, Gratuito, 202940, 10:30, 2017-08-02, 2017-08-16), 1, 202940, 202940, null, null, 1, nu

In [0]:
df_occurrence = df_occurrence.select('occurrences.id','occurrences.eventId','occurrences.rule.duration','occurrences.rule.frequency','occurrences.rule.price','occurrences.rule.spaceId','occurrences.rule.startsAt','occurrences.rule.startsOn','occurrences.rule.until')
df_occurrence = df_occurrence.toPandas()
df_occurrence.sample(20)

Out[21]:

id 
 eventId 
 duration 
 frequency 
 price 
 spaceId 
 startsAt 
 startsOn 
 until 
 
 
 
 
 444 
 2992 
 3832 
 540 
 weekly 
 Gratuita 
 6699 
 08:00 
 2018-10-01 
 2018-10-14 
 
 
 286 
 2078 
 2799 
 120 
 once 
 R$ 10.00 
 201228 
 14:00 
 2018-08-04 
 
 
 
 1360 
 5950 
 8077 
 60 
 once 
 Gratuito 
 6091 
 18:00 
 2021-01-26 
 
 
 
 781 
 3895 
 4735 
 180 
 once 
 Entrada franca 
 6114 
 14:00 
 2018-09-19 
 
 
 
 305 
 2130 
 2878 
 120 
 once 
 Gratuito 
 6091 
 19:00 
 2018-05-24 
 
 
 
 1120 
 5065 
 6023 
 0 
 weekly 
 Gratuito 
 6109 
 09:00 
 2019-08-19 
 2019-09-24 
 
 
 64 
 1297 
 2002 
 480 
 daily 
 Entrada gratuita. 
 6095 
 10:00 
 2017-02-14 
 2017-02-18 
 
 
 580 
 3365 
 4247 
 540 
 once 
 
 201228 
 09:00 
 2018-11-06 
 
 
 
 905 
 4149 
 4994 
 90 
 once 
 R$ 1 
 6103 
 11:00 
 2019-02-27 
 
 
 
 231 
 1651 
 2384 
 540 
 weekly 
 Gratuito 
 7751 
 09:00 
 2018-03-25 
 2018-04-01 
 
 
 1161 
 5214 
 6208 
 120 
 once 
 Gratuito 
 6091 
 15:00 
 2019-09-25 
 
 
 
 797 
 3913 
 4753 
 480 
 daily 
 
 6106 
 10:00 
 2018-10-18 
 2019-01-21 
 
 
 808 
 3926 
 4766 
 480 
 daily 
 
 6106 
 13:00 
 2018-10-23 
 2018-10-28 
 
 
 1090 
 4871 
 5859 
 0 
 once 
 
 6103 
 08:30 
 2019-07-09 
 
 
 
 1279 
 5502 
 6548 
 120 
 once 
 Gratuito 
 6091 
 15:00 
 2019-12-17 
 
 
 
 644 
 3589 
 4453 
 60 
 daily 
 0,00 
 6094 
 20:30 
 2018-11-28 
 2018-11-30 
 
 
 1289 
 5523 
 6574 
 120 
 once 
 Gratuito 
 6109 
 19:30 
 2019-12-05 
 
 
 
 817 
 3935 
 4776 
 480 
 daily 
 
 6106 
 12:00 
 2018-12-08 
 2018-12-09 
 
 
 349 
 2545 
 3270 
 0 
 once 
 Gratuito 
 6091 
 15:00 
 2018-07-05 
 
 
 
 165 
 1416 
 2127 
 480 
 daily 
 R$8,00 a inteira 
 201228 
 10:00 
 2017-01-01 
 2017-12-31

In [0]:
df_occurrence.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1387 entries, 0 to 1386
Data columns (total 9 columns):
 # Column Non-Null Count Dtype 
--- ------ -------------- ----- 
 0 id 1387 non-null int64 
 1 eventId 1387 non-null int64 
 2 duration 1387 non-null int64 
 3 frequency 1387 non-null object
 4 price 1387 non-null object
 5 spaceId 1387 non-null object
 6 startsAt 1387 non-null object
 7 startsOn 1387 non-null object
 8 until 1387 non-null object
dtypes: int64(3), object(6)
memory usage: 97.6+ KB

In [0]:
df_occurrence.loc[df_occurrence['frequency'] == 'once' ,'frequency'] = 'uma vez'
df_occurrence.loc[df_occurrence['frequency'] == 'daily', 'frequency'] = 'diário'
df_occurrence.loc[df_occurrence['frequency'] == 'weekly', 'frequency'] = 'semanal'

In [0]:
df_occurrence.drop_duplicates('frequency')

Out[24]:

id 
 eventId 
 duration 
 frequency 
 price 
 spaceId 
 startsAt 
 startsOn 
 until 
 
 
 
 
 0 
 739 
 1325 
 480 
 diário 
 De terça a sexta: R$ 10 e R$ 5 (meia-entrada).... 
 202940 
 10:00 
 2017-09-06 
 2017-10-22 
 
 
 1 
 742 
 1327 
 120 
 semanal 
 Gratuito 
 202940 
 11:00 
 2017-09-05 
 2017-09-19 
 
 
 4 
 745 
 1330 
 90 
 uma vez 
 Gratuito 
 202940 
 13:30 
 2017-09-14

In [0]:
df_occurrence.sample(10)

Out[25]:

id 
 eventId 
 duration 
 frequency 
 price 
 spaceId 
 startsAt 
 startsOn 
 until 
 
 
 
 
 1082 
 4862 
 5849 
 0 
 uma vez 
 
 6103 
 12:00 
 2019-06-19 
 
 
 
 1222 
 5336 
 6371 
 240 
 uma vez 
 Gratuito 
 6102 
 16:00 
 2019-08-10 
 
 
 
 625 
 3517 
 4378 
 510 
 diário 
 
 6109 
 09:00 
 2018-11-22 
 2019-01-06 
 
 
 365 
 2584 
 3311 
 540 
 uma vez 
 
 201228 
 09:00 
 2018-09-03 
 
 
 
 1031 
 4725 
 5693 
 0 
 uma vez 
 Gratuito 
 6091 
 15:00 
 2019-06-29 
 
 
 
 1180 
 5266 
 6267 
 0 
 uma vez 
 
 6103 
 10:00 
 2019-10-14 
 
 
 
 814 
 3932 
 4773 
 390 
 diário 
 
 6106 
 10:00 
 2018-11-15 
 2019-02-03 
 
 
 516 
 3242 
 4098 
 0 
 uma vez 
 Gratuito 
 6091 
 10:00 
 2018-10-18 
 
 
 
 630 
 3525 
 4390 
 60 
 uma vez 
 Grátis 
 201228 
 14:00 
 2018-10-21 
 
 
 
 997 
 4489 
 5420 
 150 
 uma vez 
 Gratuito 
 6090 
 08:30 
 2019-05-28

In [0]:
tratNulos(df_occurrence,'price','Não informado')
df_occurrence.loc[df_occurrence['price'] == 'Gratuito' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'Gratuito' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'gratuito' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'Grátis' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'grátis' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'Entrada gratuito' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'GRATUITO' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'gratuita' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'Entrada franca' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'ENTRADA FRANCA' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == '' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == '0' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == '6,00/3,00 -inteiro/meia' ,'price'] = '6,00'
df_occurrence.loc[df_occurrence['price'] == '0000' ,'price'] = '0,0'
df_occurrence.loc[df_occurrence['price'] == '00' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'livre' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'Ver site' ,'price'] = '0,00'
df_occurrence.loc[df_occurrence['price'] == 'R$6,00' ,'price'] = '6,00'
df_occurrence.loc[df_occurrence['price'] == 'R$10,00' ,'price'] = '10,00'
df_occurrence.loc[df_occurrence['price'] == 'R$50,00' ,'price'] = '50,00'
df_occurrence.loc[df_occurrence['price'] == 'R$ 1,00' ,'price'] = '1,00'
df_occurrence.loc[df_occurrence['price'] == 'R$ 1' ,'price'] = '1,00'
df_occurrence.loc[df_occurrence['price'] == 'R$ 250,00' ,'price'] = '250,00'
df_occurrence.loc[df_occurrence['price'] == 'R$175,00' ,'price'] = '175,00'
df_occurrence.loc[df_occurrence['price'] == 'Inteira/meia - R$6,00/3,00' ,'price'] = '6,00(inteira) e 3,00(meia)'
df_occurrence.loc[df_occurrence['price'] == 'R$0' ,'price'] = '0,00'


In [0]:
df_occurrence.drop_duplicates('price')

Out[27]:

id 
 eventId 
 duration 
 frequency 
 price 
 spaceId 
 startsAt 
 startsOn 
 until 
 
 
 
 
 0 
 739 
 1325 
 480 
 diário 
 De terça a sexta: R$ 10 e R$ 5 (meia-entrada).... 
 202940 
 10:00 
 2017-09-06 
 2017-10-22 
 
 
 1 
 742 
 1327 
 120 
 semanal 
 0,00 
 202940 
 11:00 
 2017-09-05 
 2017-09-19 
 
 
 24 
 803 
 1401 
 150 
 uma vez 
 R$ 40 (inteira) e R$ 20 (meia para estudantes) 
 202940 
 19:30 
 2017-08-30 
 
 
 
 41 
 826 
 1428 
 150 
 uma vez 
 R$ 40 (inteira) /R$ 20 (meia entrada estudante... 
 202940 
 19:30 
 2017-10-25 
 
 
 
 44 
 1169 
 1885 
 0 
 uma vez 
 Não informado 
 6109 
 19:00 
 2017-02-09 
 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 1307 
 5662 
 6772 
 0 
 diário 
 1000 
 16659 
 10:00 
 2020-03-23 
 2020-09-05 
 
 
 1308 
 5663 
 6773 
 240 
 diário 
 200 
 16659 
 08:00 
 2020-03-23 
 2020-03-28 
 
 
 1355 
 5942 
 8058 
 120 
 uma vez 
 5,00 
 6095 
 12:00 
 2021-12-20 
 
 
 
 1356 
 5943 
 8058 
 240 
 uma vez 
 R$ 500,00 
 6095 
 12:00 
 2021-12-20 
 
 
 
 1365 
 5955 
 8083 
 480 
 diário 
 Entrada Franca 
 21838 
 08:00 
 2022-05-16 
 2022-05-20 
 
 
 
 67 rows × 9 columns

In [0]:
df_occurrence['startOn'] = pd.to_datetime(df_occurrence['startsOn'])
df_occurrence['until'] = pd.to_datetime(df_occurrence['until'])

In [0]:
df_occurrence.sample(10)

Out[29]:

id 
 eventId 
 duration 
 frequency 
 price 
 spaceId 
 startsAt 
 startsOn 
 until 
 startOn 
 
 
 
 
 355 
 2567 
 3276 
 180 
 uma vez 
 Não informado 
 201228 
 15:00 
 2018-07-27 
 NaT 
 2018-07-27 
 
 
 438 
 2944 
 3777 
 90 
 uma vez 
 1,00 
 6103 
 12:30 
 2018-09-19 
 NaT 
 2018-09-19 
 
 
 89 
 1324 
 2029 
 0 
 diário 
 R$ 6,00 
 6106 
 10:00 
 2016-10-04 
 2017-03-31 
 2016-10-04 
 
 
 1065 
 4823 
 5806 
 0 
 uma vez 
 Não informado 
 6103 
 15:30 
 2019-05-14 
 NaT 
 2019-05-14 
 
 
 730 
 3841 
 4679 
 540 
 semanal 
 Não informado 
 6098 
 09:00 
 2018-10-09 
 2018-10-14 
 2018-10-09 
 
 
 787 
 3901 
 4741 
 60 
 uma vez 
 0,00 
 6114 
 16:00 
 2018-09-22 
 NaT 
 2018-09-22 
 
 
 529 
 3255 
 4111 
 540 
 uma vez 
 0,00 
 6699 
 08:00 
 2018-10-05 
 NaT 
 2018-10-05 
 
 
 806 
 3924 
 4764 
 150 
 uma vez 
 0,00 
 6106 
 18:30 
 2018-11-27 
 NaT 
 2018-11-27 
 
 
 425 
 2873 
 3690 
 180 
 uma vez 
 1,00 
 6103 
 18:00 
 2018-06-29 
 NaT 
 2018-06-29 
 
 
 385 
 2771 
 3562 
 180 
 uma vez 
 Não informado 
 201228 
 14:00 
 2018-08-28 
 NaT 
 2018-08-28

In [0]:
df_occurrence.drop('until',axis =1,inplace = True)
df_occurrence.drop('startOn',axis =1,inplace = True)

In [0]:
df_lab04_eventos = pd.concat([df_occurrence, df_eventos], axis = 1)

In [0]:
df_lab04_eventos = spark.createDataFrame(df_lab04_eventos)

In [0]:
df_lab04_eventos.display()

id eventId duration frequency price spaceId startsAt startsOn classificacaoEtaria descricaoSonora event_Id longDescription name shortDescription site telefonePublico traducaoLibras 739.0 1325.0 480.0 diário De terça a sexta: R$ 10 e R$ 5 (meia-entrada). Gratuito aos sábados, domingos e feriados 202940 10:00 2017-09-06 Livre Não 448.0 Oficialmente, a história do esporte começou a ser escrita nos primórdios do século XX, após a fundação do São José Futebol Clube, atual Associação Esportiva São José, ocorrida em 1913. Como não poderia ser diferente, tudo começou com o futebol - em priscas eras – denominado “o esporte bretão”, já naquele tempo, o esporte preferido dos brasileiros.

Informações colhidas do Tablóide Informativo da AESJ nos levam a saber que “por conta do interesse despertado, em São José dos Campos, transformados em “players” jovens daquela época “pentapebolavam” ora na Praça Valeriana , ora no Pátio do Cemitério, em áreas ociosas transformadas em “grounds” improvisados”.

Nascida aos pés da Serra da Mantiqueira, de bucólica cidade à “capital da tecnologia”; do futebol à natação, feminino e masculino, passando por voleibol, tênis, ciclismo, judô, atletismo, basquetebol, futebol de salão, entre tantos outros, São José dos Campos se transformaria ao longo do tempo, num dos principais exportadores de talentos esportivos do País.

Parte integrante deste contexto, o Museu de Esportes de São José dos Campos, vinculada à Secretaria de Esportes e Lazer foi criado com o intuito de resgatar a história esportiva do município, levando além-fronteiras os feitos de seus atletas através de site, palestras ao vivo, depoimento audiovisuais, troféus e exposições fotográficas. São José de todos os esportes Estrategicamente montada no corredor central, a exposição São José de todos os esportes retrata a memória esportiva da cidade a partir da fundação da Associação Esportiva São José, iniciada em 1913 até idos de 2010. Fotos, diplomas e cartazes expostos em ordem alfabética ajudam a resgatar a história do esporte de São José dos Campos, assim como a dos personagens que a representam. Não informado (12) 3921-4112 Não 742.0 1327.0 120.0 semanal 0,00 202940 11:00 2017-09-05 10 anos Não informado 473.0 Neste ano proporemos, através deste, as intervenções em sala de aula com o trabalho do poeta potiguar Antônio Francisco, cujo legado e conhecimento são consideravelmente relevantes para a produção literária potiguar, incentivando em nossos educandos a produção literária, o gosto pela leitura e, em especial, o despertar para a cultura popular, cuja qual estes podem identificar-se enquanto agentes ativos de edificação. FESTA DA POESIA Este evento surge como promotor de processos interculturais, uma vez que, há um intercâmbio entre as artes e com o ensino de literatura, pois sem a conversa com os profissionais da educação este seria inconcebível. Buscaremos, desta forma, conscientizar e aproximar o público alvo perpetuando os valores da cultura popular bastante presentes nas atuações do departamento realizadas em Patu. Não informado (84) 99667-0060 Não informado 743.0 1328.0 90.0 semanal 0,00 202940 10:30 2017-09-06 Livre Não informado 988.0 Sementes de Poesia em homenagem ao Samba e Tango - participação de Olga Valeska e Bruno Braga, uma realização do – Museu Nacional da Poesia – MUNAP sob curadoria de Regina Mello. Domingo, 16 de julho de 2017, 10h às 12h, a 108ª- edição do encontro ao ar livre com microfone aberto. Espaço MUNAP na Praça dos Fundadores, Parque Municipal René Américo Reune Giannetti. entrada franca Sementes de Poesia Neste domingo, 16 de julho de 2017 de 10 às 12h
Sementes de Poesia, microfone aberto ao público todo terceiro domingo do mês, na Praça dos Fundadores, Parque Municipal Américo René Giannetti. Av. Afonso Pena, 1377, centro, BH/MG http://www.museunacionaldapoesia.blogspot.com (31) 98838-7367 Não informado 744.0 1329.0 90.0 semanal 0,00 202940 10:30 2017-09-13 14 anos Não informado 1044.0 FUNDAÇÃO DA MEMÓRIA REPUBLIC

In [0]:
def write_AzureSQLdb():
 
    tenant_id      = 'b4920c82-7581-491a-9dab-cd2ade2f3ebd'        # Id do locatário
    MSAL_authority = 'https://login.windows.net/' + tenant_id      # Autoridade
    resource_url   = 'https://database.windows.net/.default'       # URL do recurso database
 
    # Service Principal Client ID - Criado em secrets no Key Vault
    service_principal_id = dbutils.secrets.get(scope = 'scope-adb-estudos', key = 'app-reg-adb')               
 
    # Service Principal Secret - Criado em secrets no Key Vault
    service_principal_secret = dbutils.secrets.get(scope = 'scope-adb-estudos', key = 'app-user-databricks')   
 
    # Variáveis e string de conexão ao Azure SQL Server
    jdbcHostname  = 'sql-estudo.database.windows.net'
    jdbcDatabase  = 'db-estudos'
    jdbcPort      = 1433
    jdbcUrl       = f'jdbc:sqlserver://{jdbcHostname}:{jdbcPort};database={jdbcDatabase}'    
 
    # Criando a instância que sera usada durante todo o ciclo de vida do aplicativo.
    instance     = msal.ConfidentialClientApplication(service_principal_id, service_principal_secret, MSAL_authority) 
    token        = instance.acquire_token_for_client(resource_url) # Solicitação do Token ao Azure AD.
    access_token = token['access_token']                           # Acesando o Token
 
    (df_lab04_eventos.write
       .format('jdbc')                           # Formato da Conexão
       .mode('overwrite')                        # Habilitar Sobrescrever Tabela
       .option('url', jdbcUrl)                   # URL da conexão
       .option('dbtable', 'MarcellOLiveira_LAB04.EventosLab04')                # Tabela de Inserção dos Dados
       .option('accessToken', access_token)      # Token de Acesso
       .save())

In [0]:
write_AzureSQLdb()